In [1]:
using Pkg
using JuMP
using Gurobi
#using GLPK
using XLSX
using DataFrames

In [2]:
using LinearAlgebra

In [3]:
shared_cand = DataFrame(XLSX.readtable("CandLine.xlsx", "Taul1", header=true)...) #Dataframe of shared candidate lines
int_cand =  DataFrame(XLSX.readtable("CandLineInt.xlsx", "Taul1", header=true)...) #Dataframe of internal candidate lines
shared_ex =  DataFrame(XLSX.readtable("SharedEline.xlsx", "Taul1", header=true)...) #Dataframe of shared existing lines
int_ex = DataFrame(XLSX.readtable("Tran.xlsx", "Taul1", header=true)...) #Dataframe of internal existing lines
gen =  DataFrame(XLSX.readtable("Gen.xlsx" , "Taul1", header=true)...) #Dataframe of generators
load =  DataFrame(XLSX.readtable("Load.xlsx", "Taul1", header=true)...) #Dataframe of loads
scen_prob = DataFrame(XLSX.readtable("Scenario_Probability.xlsx", "Taul1", header=true)...)
##An example of the load dataframe can be found as follows

4×2 DataFrame
 Row │ scenario  scen_weight 
     │ Any       Any         
─────┼───────────────────────
   1 │ 1         0.25
   2 │ 2         0.25
   3 │ 3         0.25
   4 │ 4         0.25

In [4]:
cand_from(i) = (shared_cand.nodeZone1 .== i)
cand_to(i) = (shared_cand.nodeZone2 .== i)
ex_from(i) = (shared_ex.nodeZone1 .== i)
ex_to(i) = (shared_ex.nodeZone2 .== i)

ex_to (generic function with 1 method)

In [5]:
l(i,s) = load[load.zoneNum .== i,[1,2,s+2]] # load within zone i and scenario s
g(i) = gen[gen.zoneNum .== i, :]   # generators within zone i
shared_c(i) = vcat(shared_cand[shared_cand.nodeZone1 .== i,:] , shared_cand[shared_cand.nodeZone2 .== i, :]) #shared candidate lines within zone i
int_c(i) = int_cand[int_cand.zoneNum .== i, :]   # number of internal candidate lines within zone i
shared_e(i) = vcat(shared_ex[shared_ex.nodeZone1 .== i,:] , shared_ex[shared_ex.nodeZone2 .== i, :]) #shared existing lines within zone i
int_e(i) =int_ex[int_ex.zoneNum .== i, :]       # internal existing lines within zone i
MC(i) = (g(i).C2 .* (g(i).PgMax .^ 2) .+ g(i).C1 .* g(i).PgMax .- g(i).C2 .*(g(i).PgMin .^ 2) .- g(i).C1 .* g(i).PgMin) ./ (g(i).PgMax .- g(i).PgMin) #Marginal cost of generators within zone i
bin_c(i) = (shared_cand.nodeZone1 .== i) + (shared_cand.nodeZone2 .== i) # A binary vector through which we can check if the shared candidate lines belong to zone i
bin_e(i) = (shared_ex.nodeZone1 .== i) + (shared_ex.nodeZone2 .== i) # A binary vector through which we can check if the shared existing lines belong to zone i
scen_weight(s) = scen_prob.scen_weight[scen_prob.scenario .== s,:]

scen_weight (generic function with 1 method)

In [6]:
S = nrow(scen_prob)

4

In [7]:
function zonal_app(i, N, S, cand_lambda, ex_lambda,shared_line_decision_var, int_line_decision_var,
        shared_cand_angle_self, shared_ex_angle_self, shared_cand_angle_1, shared_ex_angle_1, 
        shared_cand_angle_2, shared_ex_angle_2)
    
    Mod4 = Model(Gurobi.Optimizer)
    
    
    @variable(Mod4,0 <= gen_var[1:N,1:S]) # generation at each node
    @variable(Mod4,shared_cand_flow[1:nrow(shared_cand),1:S])  #Power flowing into shared candidate lines 
    @variable(Mod4,int_cand_flow[1:nrow(int_c(i)), 1:S]) #Power flowing into internal candidate lines 
    @variable(Mod4,0 <= shared_cand_angle[1:nrow(shared_cand), 1:S, 1:2]<= 2*pi) #Phase angle decision for shared candidate lines
    @variable(Mod4,0 <= int_cand_angle[1:nrow(int_c(i)), 1:S, 1:2]<= 2*pi) #Phase angle decision for internal candidate lines
    @variable(Mod4,shared_ex_flow[1:nrow(shared_ex), 1:S])  #Power flowing on shared existing shared lines
    @variable(Mod4,int_ex_flow[1:nrow(int_e(i)), 1:S])  #Power flowing on internal existing lines
    @variable(Mod4,0 <= shared_ex_angle[1:nrow(shared_ex), 1:S, 1:2]<= 2*pi) #Phase angle for existing shared lines
    @variable(Mod4,0 <= int_ex_angle[1:nrow(int_e(i)), 1:S, 1:2]<= 2*pi) #Phase angle for internal existing lines
    
    omega = 0.36;
    eta = 0.6;
    
    @expression(Mod4, total_cost, sum(scen_weight(s)[1].* sum((gen_var[n,s] .* sum((g(i).gNodeID .== n) .* MC(i))) for n in 1:N)
        .+ sum(sum(eta * shared_ex_angle[h,s,1] .* (shared_ex_angle_self[h,s,1] .- shared_ex_angle_1[h,s,1]) .+
            eta * shared_ex_angle[h,s,1] .* (shared_ex_angle_self[h,s,1] .- shared_ex_angle_2[h,s,1]) .+
            eta * shared_ex_angle[h,s,2] .* (shared_ex_angle_self[h,s,2] .- shared_ex_angle_1[h,s,2]) .+
            eta * shared_ex_angle[h,s,2] .* (shared_ex_angle_self[h,s,2] .- shared_ex_angle_2[h,s,2]) .+
            shared_ex_angle[h,s,1] .* ex_lambda[h,s,1] .+ 
            shared_ex_angle[h,s,2] .* ex_lambda[h,s,2] for h in 1:nrow(shared_ex))) .+
            sum(sum((omega /2) * (shared_ex_angle[:,s,1] .- shared_ex_angle_self[:,s,1]) .^ 2)) .+
            sum(sum((omega /2) * (shared_ex_angle[:,s,2] .- shared_ex_angle_self[:,s,2]) .^ 2))
        .+ sum(sum(eta * shared_cand_angle[c,s,1] .* (shared_cand_angle_self[c,s,1] .- shared_cand_angle_1[c,s,1]) .+
            eta * shared_cand_angle[c,s,1] .* (shared_cand_angle_self[c,s,1] .- shared_cand_angle_2[c,s,1]) .+
            eta * shared_cand_angle[c,s,2] .* (shared_cand_angle_self[c,s,2] .- shared_cand_angle_1[c,s,2]) .+
            eta * shared_cand_angle[c,s,2] .* (shared_cand_angle_self[c,s,2] .- shared_cand_angle_2[c,s,2]) .+
            shared_cand_angle[c,s,1] .* cand_lambda[c,s,1] .+ 
            shared_cand_angle[c,s,2] .* cand_lambda[c,s,2] for c in 1:nrow(shared_cand))) .+
            sum(sum((omega /2) * (shared_cand_angle[:,s,1] .- shared_cand_angle_self[:,s,1]) .^ 2)) .+
            sum(sum((omega /2) * (shared_cand_angle[:,s,2] .- shared_cand_angle_self[:,s,2]) .^ 2)) for s in 1:S))
            
            
    for s in 1:S        
            
        for n in 1:N
            # Power balance constraint for each node
            @constraint(Mod4,  sum((g(i).gNodeID .== n) .* gen_var[n,s]) .+ sum(l(i,s)[:,3].* (l(i,s).lNodeID .== n)) .==
                sum((shared_cand.tNodeID1 .== n) .*bin_c(i) .* shared_cand_flow[:,s]) .- sum((shared_cand.tNodeID2 .== n) .* bin_c(i) .* shared_cand_flow[:,s]) .+
                sum((shared_ex.tNodeID1 .== n) .* bin_e(i) .* shared_ex_flow[:,s]) .- sum((shared_ex.tNodeID2 .== n) .* bin_e(i) .* shared_ex_flow[:,s]) .+
                sum((int_c(i).tNodeID1 .== n) .* int_cand_flow[:,s]) .- sum((int_c(i).tNodeID2 .== n) .* int_cand_flow[:,s]) .+
                sum((int_e(i).tNodeID1 .== n) .* int_ex_flow[:,s]) .- sum((int_e(i).tNodeID2 .== n) .* int_ex_flow[:,s]))
            #Lower limit for generation of each node
            @constraint(Mod4, sum(g(i).gNodeID .== n) .* gen_var[n,s] .<= sum((g(i).gNodeID .== n) .* g(i).PgMax))
            #Upper limit for generation of each node
            @constraint(Mod4, sum((g(i).gNodeID .== n) .* g(i).PgMin) .<= sum(g(i).gNodeID .== n) .* gen_var[n,s])
        end

        M=100 #Big number

        #Constraints elated to the candidate shared lines:
        for c in 1:nrow(shared_cand) 
            #Associating the power flowing within the line with the phase angles of nodes:
            @constraint(Mod4,-M .* (1 .- bin_c(i) .* shared_line_decision_var[c]) .<= bin_c(i) .* shared_cand_flow[c,s] .- ((1 ./ shared_cand.reacT[c]) .* (bin_c(i) .* shared_cand_angle[c,s,1] .- bin_c(i) .* shared_cand_angle[c,s,2])))

            @constraint(Mod4, bin_c(i) .* shared_cand_flow[c,s] .- ((1 ./ shared_cand.reacT[c]) .* (bin_c(i) .* shared_cand_angle[c,s,1] .- bin_c(i) .* shared_cand_angle[c,s,2])) .<= M .* (1 .- bin_c(i) .* shared_line_decision_var[c]))
            #limiting the upper bound of power flow flowing within candidate shared lines
            @constraint(Mod4, bin_c(i) .* shared_cand_flow[c,s] .<= bin_c(i) .* shared_line_decision_var[c] .* shared_cand.ptMax[c])
            #Limiting the lower bound of power flowing within the candidate shared lines
            @constraint(Mod4, -shared_cand.ptMax[c] .* bin_c(i) .* shared_line_decision_var[c] .<= bin_c(i) .* shared_cand_flow[c,s])
            #@constraint(Mod4, shared_cand_angle[5,2] .== 0)
        end

        #The same constraints related to the candidate internal lines:
        for c in 1:nrow(int_c(i))
            @constraint(Mod4,-M .* (1 .- int_line_decision_var[c]) .<= int_cand_flow[c,s] .- ((1 ./ int_c(i).reacT[c]) .* (int_cand_angle[c,s,1] .- int_cand_angle[c,s,2])))
            @constraint(Mod4, int_cand_flow[c,s] .- ((1 ./ int_c(i).reacT[c]) .* (int_cand_angle[c,s,1] .- int_cand_angle[c,s,2])) .<= M .* (1 .- int_line_decision_var[c]))
            @constraint(Mod4, int_cand_flow[c,s] .<= int_line_decision_var[c] .* int_c(i).ptMax[c])
            @constraint(Mod4, -int_c(i).ptMax[c] .*int_line_decision_var[c] .<= int_cand_flow[c,s])
        end

        #The same constraints related to the shared existing lines:
        for h in 1:nrow(shared_ex)
            @constraint(Mod4, bin_e(i) .* shared_ex_flow[h,s] .== (1 ./ shared_ex.reacT[h]) .* (bin_e(i) .* shared_ex_angle[h,s,1] .- bin_e(i) .* shared_ex_angle[h,s,2]))
            @constraint(Mod4, bin_e(i) .* shared_ex_flow[h,s] .<= bin_e(i) .* shared_ex. ptMax[h])
            @constraint(Mod4, bin_e(i) .* -shared_ex.ptMax[h] .<= bin_e(i) .* shared_ex_flow[h,s])
            #@constraint(Mod4, shared_ex_angle[1,2] .== 0)
            #@constraint(Mod4, shared_ex_angle[7,2] .== 0)

        end
        #The same constraints related to the internal existing lines:

        for h in 1:nrow(int_e(i))
            @constraint(Mod4, int_ex_flow[h,s] .== (1 ./ int_e(i).reacT[h]) .* (int_ex_angle[h,s,1] .- int_ex_angle[h,s,2]))
            @constraint(Mod4, int_ex_flow[h,s] .<= int_e(i).ptMax[h])
            @constraint(Mod4, -int_e(i).ptMax[h] .<= int_ex_flow[h,s])
        end
    end
    #The model objective is to minimize the total cost:
    
    @objective(Mod4, Min, total_cost)
    optimize!(Mod4)
    if termination_status(Mod4) == MOI.OPTIMAL #If the solution is optimal then it returns the variables
    
        shared_cand_power = value.(shared_cand_flow)
        shared_cand_phase_angle = value.(shared_cand_angle)
        shared_ex_power = value.(shared_ex_flow)
        shared_ex_phase_angle = value.(shared_ex_angle)
        gen_power = value.(gen_var)
        int_cand_power = value.(int_cand_flow)
        int_cand_phase_angle = value.(int_cand_angle)
        obj_value = objective_value(Mod4)
        generation = value.(gen_var)
        [obj_value, shared_cand_power,shared_cand_phase_angle,shared_ex_power,shared_ex_phase_angle,gen_power, int_cand_power, int_cand_phase_angle, generation]

    end
end
    
    

zonal_app (generic function with 1 method)

In [8]:
f=ones(12000)
h=0
cand_lambda_1= zeros(12000,nrow(shared_cand),S,2)
ex_lambda_1 = zeros(12000,nrow(shared_ex),S,2)
cand_lambda_2= zeros(12000,nrow(shared_cand),S,2)
ex_lambda_2 = zeros(12000,nrow(shared_ex),S,2)
cand_lambda_3= zeros(12000,nrow(shared_cand),S,2)
ex_lambda_3 = zeros(12000,nrow(shared_ex),S,2)
cand_angle_1 = zeros(12000,nrow(shared_cand),S,2)
c_angle_1 = zeros(12000,nrow(shared_cand),S,2)
cand_angle_2 = zeros(12000,nrow(shared_cand),S,2)
c_angle_2 = zeros(12000,nrow(shared_cand),S,2)
cand_angle_3 = zeros(12000,nrow(shared_cand),S,2)
c_angle_3 = zeros(12000,nrow(shared_cand),S,2)

ex_angle_1 = zeros(12000,nrow(shared_ex),S,2)
e_angle_1 = zeros(12000,nrow(shared_ex),S,2)
ex_angle_2 = zeros(12000,nrow(shared_ex),S,2)
e_angle_2 = zeros(12000,nrow(shared_ex),S,2)
ex_angle_3 = zeros(12000,nrow(shared_ex),S,2)
e_angle_3 = zeros(12000,nrow(shared_ex),S,2)

cand_flow_1 =zeros(12000,nrow(shared_cand),S)
cand_flow_2 =zeros(12000,nrow(shared_cand),S)
cand_flow_3 =zeros(12000,nrow(shared_cand),S)
ex_flow_1 = zeros(12000,nrow(shared_ex),S)
ex_flow_2 = zeros(12000,nrow(shared_ex),S)
ex_flow_3 = zeros(12000,nrow(shared_ex),S)

gen_1 = zeros(12000,nrow(g(1)),S)
gen_2 = zeros(12000,nrow(g(2)),S)
gen_3 = zeros(12000,nrow(g(3)),S)



shared_line_decision_var_m =  
[-0.0
 -0.0
  1.0
  1.0
  1.0
 -0.0]
int_line_decision_var_1 =
[0.0
  1.0
  1.0
 -0.0
  1.0
  1.0
 -0.0
 -0.0
 -0.0
  1.0]
int_line_decision_var_2 =
[0.0
 -0.0
 -0.0
 -0.0
 -0.0
  1.0
  1.0
 -0.0
 -0.0
  1.0
  1.0
 -0.0
 -0.0
 -0.0
 -0.0
 -0.0
 -0.0
 -0.0]
int_line_decision_var_3 =
[-0.0
 -0.00]

2-element Vector{Float64}:
 -0.0
 -0.0

In [9]:
    j = 2
    for j in 2:1000    # It considers 1000 iteration
        if abs(f[j-1]) > 0.00001  
         
            R_1 = zonal_app(1, 14, S, cand_lambda_1[j,:,:,:], ex_lambda_1[j,:,:,:],shared_line_decision_var_m, int_line_decision_var_1,
            cand_angle_1[j-1,:,:,:], ex_angle_1[j-1,:,:,:], cand_angle_2[j-1,:,:,:],  ex_angle_2[j-1,:,:,:], 
            cand_angle_3[j-1,:,:,:], ex_angle_3[j-1,:,:,:])
        
            R_2 = zonal_app(2, 30, S, cand_lambda_2[j,:,:,:], ex_lambda_2[j,:,:,:],shared_line_decision_var_m, int_line_decision_var_2,
            cand_angle_2[j-1,:,:,:], ex_angle_2[j-1,:,:,:], cand_angle_1[j-1,:,:,:], ex_angle_1[j-1,:,:,:], 
            cand_angle_3[j-1,:,:,:], ex_angle_3[j-1,:,:,:])       
        
            R_3 = zonal_app(3, 5, S, cand_lambda_3[j,:,:,:], ex_lambda_3[j,:,:,:],shared_line_decision_var_m, int_line_decision_var_3,
            cand_angle_3[j-1,:,:,:], ex_angle_3[j-1,:,:,:], cand_angle_1[j-1,:,:,:],  ex_angle_1[j-1,:,:,:], 
            cand_angle_2[j-1,:,:,:], ex_angle_2[j-1,:,:,:])
        
        
            cand_lambda_1[j+1,:,:,:] .= bin_c(1) .* cand_lambda_1[j,:,:,:] .+ 0.1 * bin_c(1) .* (R_1[3] .- (bin_c(2) .* R_2[3] .+ bin_c(3) .* R_3[3]))
            cand_lambda_2[j+1,:,:,:] .= bin_c(2) .* cand_lambda_2[j,:,:,:] .+ 0.1 * bin_c(2) .* (R_2[3] .- (bin_c(1) .* R_1[3] .+ bin_c(3) .* R_3[3]))
            cand_lambda_3[j+1,:,:,:] .= bin_c(3) .* cand_lambda_3[j,:,:,:] .+ 0.1 * bin_c(3) .* (R_3[3] .- (bin_c(1) .* R_1[3] .+ bin_c(2) .* R_2[3]))
        
        
    
            ex_lambda_1[j+1,:,:,:] .= bin_e(1) .* ex_lambda_1[j,:,:,:] .+ 0.1 * (bin_e(1) .* R_1[5] .- (bin_e(2) .* R_2[5] .+ bin_e(3) .* R_3[5]))
            ex_lambda_2[j+1,:,:,:] .= bin_e(2) .* ex_lambda_2[j,:,:,:] .+ 0.1 * (bin_e(2) .* R_2[5] .- (bin_e(1) .* R_1[5] .+ bin_e(3) .* R_3[5]))
            ex_lambda_3[j+1,:,:,:] .= bin_e(3) .* ex_lambda_3[j,:,:,:] .+ 0.1 * (bin_e(3) .* R_3[5] .- (bin_e(1) .* R_1[5] .+ bin_e(2) .* R_2[5]))
        
            f[j] = sum(sum((bin_c(1) .* R_1[3] .- (bin_c(2) .* R_2[3] .+ bin_c(3) .* R_3[3])).^ 2)) +
                    sum(sum((bin_c(2) .* R_2[3] .- (bin_c(1) .* R_1[3] .+ bin_c(3) .* R_3[3])).^ 2)) +
                    sum(sum((bin_c(3) .* R_3[3] .- (bin_c(1) .* R_1[3] .+ bin_c(2) .* R_2[3])).^ 2)) +
                    sum(sum((bin_e(1) .* R_1[5] .- (bin_e(2) .* R_2[5] .+ bin_e(3) .* R_3[5])).^ 2)) +
                    sum(sum((bin_e(2) .* R_2[5] .- (bin_e(1) .* R_1[5] .+ bin_e(3) .* R_3[5])).^ 2)) +
                    sum(sum((bin_e(3) .* R_3[5] .- (bin_e(2) .* R_2[5] .+ bin_e(1) .* R_1[5])).^ 2))
        
            c_angle_1 = R_1[3]
            c_angle_2 = R_2[3]
            c_angle_3 = R_3[3]
        
            e_angle_1 = R_1[5]
            e_angle_2 = R_2[5]
            e_angle_3 = R_3[5]
            
            cand_flow_1 = R_1[2]
            cand_flow_2 = R_2[2]
            cand_flow_3 = R_3[2]
        
            ex_flow_1 = R_1[4]
            ex_flow_2 = R_2[4]
            ex_flow_3 = R_3[4]
        
            gen_1 = R_1[9]
            gen_2 = R_2[9]
            gen_3 = R_3[9]
            
            
            h= R_2[1] + R_1[1] + R_3[1]
            
            if isdefined(Main, :IJulia)
                Main.IJulia.stdio_bytes[] = 0
            end
        
            print('*') 
        
        else
            print(h)
            print(c_angle_1)
            print(c_angle_2)
            print(c_angle_3)
            print(e_angle_1)
            print(e_angle_2)
            print(e_angle_3)
        end
    end
    

Academic license - for non-commercial use only - expires 2023-06-28
Gurobi Optimizer version 9.1.2 build v9.1.2rc0 (win64)
Thread count: 4 physical cores, 4 logical processors, using up to 4 threads
Optimize a model with 1912 rows, 584 columns and 2608 nonzeros
Model fingerprint: 0xc22a3fa9
Model has 112 quadratic objective terms
Coefficient statistics:
  Matrix range     [1e+00, 2e+01]
  Objective range  [9e+00, 1e+01]
  QObjective range [4e-01, 4e-01]
  Bounds range     [6e+00, 6e+00]
  RHS range        [9e-01, 3e+02]
Presolve removed 1857 rows and 429 columns
Presolve time: 0.02s
Presolved: 55 rows, 159 columns, 282 nonzeros
Presolved model has 56 quadratic objective terms
Ordering time: 0.00s

Barrier statistics:
 AA' NZ     : 9.900e+01
 Factor NZ  : 3.550e+02
 Factor Ops : 3.111e+03 (less than 1 second per iteration)
 Threads    : 1

                  Objective                Residual
Iter       Primal          Dual         Primal    Dual     Compl     Time
   0   1.16878124e+07 -

In [10]:
h #OF of the second stage

2343.8657017969585

In [11]:
f[300]

1533.9208416003537

In [12]:
c_angle_1

6×4×2 Array{Float64, 3}:
[:, :, 1] =
 0.000323349  0.000323349  0.000323349  0.000323349
 0.0          0.0          0.0          0.0
 4.04593      1.07135      1.81085      0.535674
 5.75         5.75         5.75         3.5616
 0.0          0.0          0.0          0.0
 0.0          0.0          0.0          0.0

[:, :, 2] =
 0.000323349  0.000323349  0.000323349  0.000323349
 0.0          0.0          0.0          0.0
 5.64479e-6   1.77121e-6   1.76658e-6   1.76326e-6
 7.77057e-11  7.77059e-11  7.77059e-11  1.25474e-10
 0.0          0.0          0.0          0.0
 0.0          0.0          0.0          0.0

In [13]:
c_angle_2

6×4×2 Array{Float64, 3}:
[:, :, 1] =
 0.000330612  0.000330612  0.000330612  0.000330612
 0.0          0.0          0.0          0.0
 0.0          0.0          0.0          0.0
 5.75         5.75         5.75         3.5616
 4.7814       1.28387      2.02924      0.641933
 0.0          0.0          0.0          0.0

[:, :, 2] =
 0.000330612  0.000330612  0.000330612  0.000330612
 0.0          0.0          0.0          0.0
 0.0          0.0          0.0          0.0
 1.28741e-6   1.2684e-6    1.52966e-6   1.06328e-6
 1.0803e-6    1.14844e-6   1.21779e-6   1.25407e-6
 0.0          0.0          0.0          0.0

In [14]:
c_angle_3

6×4×2 Array{Float64, 3}:
[:, :, 1] =
 0.00032335   0.00032335   0.00032335   0.00032335
 0.0          0.0          0.0          0.0
 4.04593      1.07135      1.81085      0.535674
 0.000243309  0.000243309  0.000243309  0.000243309
 4.7814       1.28387      2.02924      0.641933
 0.0          0.0          0.0          0.0

[:, :, 2] =
 0.00032335   0.00032335   0.00032335   0.00032335
 0.0          0.0          0.0          0.0
 8.97656e-11  3.3933e-10   2.00648e-10  6.79565e-10
 0.000243309  0.000243309  0.000243309  0.000243309
 7.59487e-11  2.83056e-10  1.79014e-10  5.66751e-10
 0.0          0.0          0.0          0.0

In [15]:
e_angle_3 

8×4×2 Array{Float64, 3}:
[:, :, 1] =
 3.49066      3.49066      3.49066      0.421382
 0.000150667  0.000150991  0.000150867  0.000150904
 0.0          0.0          0.0          0.0
 0.000322739  0.000322737  0.000322758  0.000322626
 4.61432      3.54081      5.12795      1.77041
 4.06576      1.06047      1.79247      0.530237
 0.000296155  0.000292117  0.000294031  0.00028506
 9.56304e-11  3.56417e-10  2.25413e-10  7.13818e-10

[:, :, 2] =
 3.29337e-7   3.21768e-7   3.59234e-7   3.28034e-7
 0.000150853  0.000150573  0.00015068   0.000150666
 0.0          0.0          0.0          0.0
 0.000323827  0.00032395   0.000323905  0.000324066
 7.87049e-11  1.02576e-10  7.08213e-11  2.05235e-10
 9.08239e-11  3.42791e-10  2.02686e-10  6.86518e-10
 0.000278922  0.000285689  0.000282961  0.000293264
 3.79753      1.01969      1.61168      0.509843

In [16]:
e_angle_2

8×4×2 Array{Float64, 3}:
[:, :, 1] =
 6.28318      6.28318      6.28318      0.758488
 0.000271201  0.000271785  0.00027156   0.000271627
 0.0          0.0          0.0          0.0
 0.000179299  0.000179298  0.00017931   0.000179237
 2.56351      1.96712      2.84886      0.983559
 4.06576      1.06047      1.79247      0.530237
 0.000296155  0.000292116  0.000294031  0.000285059
 1.0444e-6    9.64585e-7   1.13069e-6   1.15066e-6

[:, :, 2] =
 1.1845e-6    1.15733e-6   1.29194e-6   1.17929e-6
 0.000271535  0.000271031  0.000271224  0.000271199
 0.0          0.0          0.0          0.0
 0.000179904  0.000179972  0.000179947  0.000180037
 0.000327551  0.000327522  0.000326569  0.000329056
 2.03943e-9   1.2669e-6    1.15467e-6   1.31007e-6
 0.000278921  0.000285689  0.000282961  0.000293264
 3.79753      1.01969      1.61168      0.509843

In [17]:
e_angle_1

8×4×2 Array{Float64, 3}:
[:, :, 1] =
 6.28319      6.28319      6.28319      0.758488
 0.000271201  0.000271784  0.000271559  0.000271627
 0.0          0.0          0.0          0.0
 0.000322739  0.000322736  0.000322758  0.000322626
 4.61432      3.54081      5.12795      1.77041
 2.25875      0.589152     0.995816     0.294576
 0.000164531  0.000162287  0.000163351  0.000158366
 2.90401e-7   2.68266e-7   3.14451e-7   3.20109e-7

[:, :, 2] =
 1.01471e-11  1.01273e-11  1.01471e-11  5.89969e-10
 0.000271535  0.00027103   0.000271223  0.000271199
 0.0          0.0          0.0          0.0
 0.000323827  0.00032395   0.000323905  0.000324066
 7.71959e-6   1.7562e-6    4.29847e-6   1.75504e-6
 5.9177e-10   3.52327e-7   3.2108e-7    3.64426e-7
 0.000154957  0.000158716  0.000157201  0.000162924
 2.10974      0.566492     0.895379     0.283246

In [18]:
cand_flow_1

6×4 Matrix{Float64}:
   0.0       0.0        0.0       0.0
   0.0       0.0        0.0       0.0
  20.4371    5.41166    9.14708   2.70582
 100.0     100.0      100.0      61.9408
   0.0       0.0        0.0       0.0
   0.0       0.0        0.0       0.0

In [19]:
cand_flow_2

6×4 Matrix{Float64}:
   0.0       0.0        0.0      0.0
   0.0       0.0        0.0      0.0
   0.0       0.0        0.0      0.0
 100.0     100.0      100.0     61.9408
  28.9431    7.77158   12.2835   3.88578
   0.0       0.0        0.0      0.0

In [20]:
cand_flow_3

6×4 Matrix{Float64}:
  0.0     0.0       0.0      0.0
  0.0     0.0       0.0      0.0
 20.4371  5.41166   9.14709  2.70583
  0.0     0.0       0.0      0.0
 28.9431  7.77158  12.2835   3.88579
  0.0     0.0       0.0      0.0

In [21]:
ex_flow_1

8×4 Matrix{Float64}:
  23.2711      23.2711      23.2711       2.80921
  -1.01522e-6   2.2901e-6    1.02141e-6   1.29948e-6
   0.0          0.0          0.0          0.0
  -1.95765e-6  -2.1825e-6   -2.06278e-6  -2.59043e-6
  77.0335      59.112       85.6085      29.556
  11.2938       2.94576      4.97908      1.47288
   8.70374e-5   3.24609e-5   5.59088e-5  -4.14378e-5
 -10.143       -2.72352     -4.3047      -1.36176

In [22]:
ex_flow_2

8×4 Matrix{Float64}:
  23.271        23.271       23.271         2.80921
  -1.01522e-6    2.2901e-6    1.02141e-6    1.29948e-6
   0.0           0.0          0.0           0.0
  -1.08758e-6   -1.2125e-6   -1.14599e-6   -1.43913e-6
  42.791        32.8346      47.5549       16.4145
  20.3288        5.30236      8.96234       2.65118
   0.000156667   5.84297e-5   0.000100636  -7.45881e-5
 -18.2574       -4.90233     -7.74847      -2.45116

In [23]:
ex_flow_3

8×4 Matrix{Float64}:
  12.9284       12.9284      12.9284        1.56067
  -5.6401e-7     1.27228e-6   5.67448e-7    7.21931e-7
   0.0           0.0          0.0           0.0
  -1.95765e-6   -2.1825e-6   -2.06277e-6   -2.59043e-6
  77.0337       59.112       85.6086       29.556
  20.3288        5.30237      8.96234       2.65118
   0.000156667   5.84296e-5   0.000100636  -7.4588e-5
 -18.2574       -4.90234     -7.74847      -2.45117

In [24]:
gen_1

14×4 Matrix{Float64}:
 135.729        6.22894      70.9789       3.81637e-11
   6.21643e-11  6.21643e-11   6.21643e-11  2.36466e-11
   0.0          0.0           0.0          0.0
   0.0          0.0           0.0          0.0
   0.0          0.0           0.0          0.0
   0.0          0.0           0.0          0.0
   0.0          0.0           0.0          0.0
   0.0          0.0           0.0          0.0
   0.0          0.0           0.0          0.0
   0.0          0.0           0.0          0.0
   0.0          0.0           0.0          0.0
   0.0          0.0           0.0          0.0
   0.0          0.0           0.0          0.0
   0.0          0.0           0.0          0.0

In [25]:
gen_2

30×4 Matrix{Float64}:
 19.8269        4.01605e-9   15.3454        8.92455e-10
 80.0          80.0          80.0          47.3
  0.0           0.0           0.0           0.0
  0.0           0.0           0.0           0.0
  0.0           0.0           0.0           0.0
  0.0           0.0           0.0           0.0
  0.0           0.0           0.0           0.0
  0.0           0.0           0.0           0.0
  0.0           0.0           0.0           0.0
  0.0           0.0           0.0           0.0
  0.0           0.0           0.0           0.0
  0.0           0.0           0.0           0.0
 40.0          14.6          40.0           1.14744e-9
  ⋮                                        
  0.0           0.0           0.0           0.0
  0.0           0.0           0.0           0.0
  0.0           0.0           0.0           0.0
 49.3731        2.40482e-9    6.55463       7.76798e-10
  4.83861e-9    1.60642e-9    4.83861e-9    6.69341e-10
  0.0           0.0           0.0      

In [26]:
gen_3

5×4 Matrix{Float64}:
 7.48945e-11  6.66326e-11  6.84724e-11  6.53605e-11
 3.01692e-11  2.8734e-11   2.90708e-11  2.84948e-11
 0.0          0.0          0.0          0.0
 0.0          0.0          0.0          0.0
 0.0          0.0          0.0          0.0

In [27]:
show(stdout, "text/plain", gen_2)

30×4 Matrix{Float64}:
 19.8269        4.01605e-9   15.3454        8.92455e-10
 80.0          80.0          80.0          47.3
  0.0           0.0           0.0           0.0
  0.0           0.0           0.0           0.0
  0.0           0.0           0.0           0.0
  0.0           0.0           0.0           0.0
  0.0           0.0           0.0           0.0
  0.0           0.0           0.0           0.0
  0.0           0.0           0.0           0.0
  0.0           0.0           0.0           0.0
  0.0           0.0           0.0           0.0
  0.0           0.0           0.0           0.0
 40.0          14.6          40.0           1.14744e-9
  0.0           0.0           0.0           0.0
  0.0           0.0           0.0           0.0
  0.0           0.0           0.0           0.0
  0.0           0.0           0.0           0.0
  0.0           0.0           0.0           0.0
  0.0           0.0           0.0           0.0
  0.0           0.0           0.0           0.0
  0